#  Consignes

## Description

Ouvrir le fichier ks-projects-201801.csv, il recense environ 100 000 projets KickStarter. Intégrer les données directement avec L'API Python dans une base de données Mongo. 

Il conviendra de bien spécifier manuellement l'ID du document. Pensez aussi à bien formatter le type des données pour profiter des méthodes implémentées par Mongo. L'ensemble de données n'est pas forcément nécessaire, c'est à vous de créer votre modèle de données.

## Questions

- 1) Récupérer les 5 projets ayant reçu le plus de promesse de dons.
- 2) Compter le nombre de projets ayant atteint leur but.
- 3) Compter le nombre de projets pour chaque catégorie.
- 4) Compter le nombre de projets français ayant été instanciés avant 2016.
- 5) Récupérer les projets américains ayant demandé plus de 200 000 dollars.
- 6) Compter le nombre de projet ayant "Sport" dans leur nom

In [15]:
import pandas as pd
import pymongo
from pymongo import MongoClient

In [16]:
client = pymongo.MongoClient()
database = client['exercices']
collection = database['kickstarter']

In [17]:
df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")
df_ks.head(10)

C:\Users\owenb\AppData\Local\Temp\ipykernel_15540\182781903.py:1: DtypeWarning: Columns (6,8,10,12) have mixed types. Specify dtype option on import or set low_memory=False.
  df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")


ID                                               name  \
0   872782264    Scott Cooper's Solo CD "A Leg Trick" (Canceled)   
1  1326492673                                    Ohceola jewelry   
2  1688410639  Sluff Off & Harald: Two latest EGGs are Classi...   
3   156812982  SketchPlanner: Create and Plan- all in one bea...   
4  1835968190    Proven sales with custom motorcycle accessories   
5  1771789139                                   Room For Growth!   
6  1301627822          Build a mini Udemy with Laravel and Vuejs   
7   881336601                                         Applitizer   
8  1669374237  Help I Am Wolves fund their first album "ABCD"...   
9   556821416        Eco  Bamboo Underwear funding....GOT WOOD ?   

         category main_category currency    deadline      goal  \
0            Rock         Music      USD  2011-09-16    2000.0   
1         Fashion       Fashion      USD  2012-08-22   18000.0   
2  Tabletop Games         Games      USD  2016-07-19    2000.0   
3       Art Books    Publishing      USD  2017-09-27   13000.0   
4       Sculpture           Art      CAD  2016-02-24    5000.0   
5         Couture       Fashion      USD  2016-05-02    2000.0   
6             Web    Technology      CAD  2018-01-11    3000.0   
7        Software    Technology      HKD  2017-08-20  100000.0   
8           Music         Music      EUR  2017-12-04    1000.0   
9         Fashion       Fashion      GBP  2012-12-13    9500.0   

              launched  pledged       state backers country  usd pledged  \
0  2011-08-17 06:31:31   1145.0    canceled      24      US       1145.0   
1  2012-07-23 20:46:48   1851.0      failed      28      US       1851.0   
2  2016-07-01 21:55:54   7534.0  successful     254      US       3796.0   
3  2017-08-28 15:47:02  16298.0  successful     367      US       2670.0   
4  2016-01-25 17:37:10      1.0      failed       1      CA     0.708148   
5  2016-04-11 18:15:00      6.0      failed       2      US          6.0   
6  2017-12-12 01:37:26    155.0        live       7      CA    15.563996   
7  2017-07-21 16:50:05   1000.0      failed       1      HK    128.08538   
8  2017-10-27 16:55:47   1465.0  successful      46      BE          0.0   
9  2012-11-13 10:58:34   1212.0      failed      43      GB  1928.137119   

   usd_pledged_real  
0       1145.000000  
1       1851.000000  
2       7534.000000  
3      16298.000000  
4          0.738225  
5          6.000000  
6        123.811806  
7        127.831467  
8       1720.210418  
9       1953.672808

Ce warning intervient lorsque pandas n'arrive pas à inférer le type de données. Il est sympa il précise les colones 6,8,10,12. 

In [18]:
df_ks.columns[[6,8,10,12]]

Index(['goal', 'pledged', 'backers', 'usd pledged'], dtype='object')

## Question 0

### Netoyer les données

In [19]:
client = MongoClient('localhost', 27017)  
db = client['kickstarter_db']
collection = db['projects']

projects = df_ks.to_dict(orient='records')

### Importer les données

In [20]:
collection.insert_many(projects)

InsertManyResult([ObjectId('678e296171ed4cb9b9b105a3'), ObjectId('678e296171ed4cb9b9b105a4'), ObjectId('678e296171ed4cb9b9b105a5'), ObjectId('678e296171ed4cb9b9b105a6'), ObjectId('678e296171ed4cb9b9b105a7'), ObjectId('678e296171ed4cb9b9b105a8'), ObjectId('678e296171ed4cb9b9b105a9'), ObjectId('678e296171ed4cb9b9b105aa'), ObjectId('678e296171ed4cb9b9b105ab'), ObjectId('678e296171ed4cb9b9b105ac'), ObjectId('678e296171ed4cb9b9b105ad'), ObjectId('678e296171ed4cb9b9b105ae'), ObjectId('678e296171ed4cb9b9b105af'), ObjectId('678e296171ed4cb9b9b105b0'), ObjectId('678e296171ed4cb9b9b105b1'), ObjectId('678e296171ed4cb9b9b105b2'), ObjectId('678e296171ed4cb9b9b105b3'), ObjectId('678e296171ed4cb9b9b105b4'), ObjectId('678e296171ed4cb9b9b105b5'), ObjectId('678e296171ed4cb9b9b105b6'), ObjectId('678e296171ed4cb9b9b105b7'), ObjectId('678e296171ed4cb9b9b105b8'), ObjectId('678e296171ed4cb9b9b105b9'), ObjectId('678e296171ed4cb9b9b105ba'), ObjectId('678e296171ed4cb9b9b105bb'), ObjectId('678e296171ed4cb9b9b105

## Question 1  

In [21]:
# Récupérer les 5 projets ayant reçu le plus de promesse de dons
top_5_projects = collection.find().sort('usd pledged', -1).limit(5)

for project in top_5_projects:
    print(f"Nom: {project['name']}, Promesse de dons: {project['usd pledged']}")

Nom: Debut Album from Michael Adam , Promesse de dons: US
Nom: THE SHELLS ï¿½ AUSFLUG NACH NEU-FRIEDENWALD, Promesse de dons: 9999.268739
Nom: True North ï¿½ Repurposed Sailcloth Products, Promesse de dons: 9996.0
Nom: Holo ï¿½ Smartphone & Tablet Hologram, Promesse de dons: 9994.32696132
Nom: 2016 Gaming Calendar, Promesse de dons: 9994.0


## Question 2

In [22]:
reached_goal_count = collection.count_documents({'state': 'successful'})
print(f"Nombre de projets ayant atteint leur but : {reached_goal_count}")

Nombre de projets ayant atteint leur but : 53040


## Question 3

In [23]:
category_counts = collection.aggregate([
    {'$group': {'_id': '$category', 'count': {'$sum': 1}}}
])

for category in category_counts:
    print(f"Catégorie: {category['_id']}, Nombre de projets: {category['count']}")

Catégorie: Tabletop Games, Nombre de projets: 5581
Catégorie: Performance Art, Nombre de projets: 855
Catégorie: Glass, Nombre de projets: 51
Catégorie: Gadgets, Nombre de projets: 1210
Catégorie: Family, Nombre de projets: 130
Catégorie: Comics, Nombre de projets: 1931
Catégorie: Camera Equipment, Nombre de projets: 165
Catégorie: Installations, Nombre de projets: 178
Catégorie: Digital Art, Nombre de projets: 524
Catégorie: Thrillers, Nombre de projets: 302
Catégorie: Drinks, Nombre de projets: 995
Catégorie: Nonfiction, Nombre de projets: 3390
Catégorie: Painting, Nombre de projets: 1288
Catégorie: Experimental, Nombre de projets: 357
Catégorie: Space Exploration, Nombre de projets: 137
Catégorie: Community Gardens, Nombre de projets: 115
Catégorie: Drama, Nombre de projets: 871
Catégorie: Software, Nombre de projets: 1194
Catégorie: Zines, Nombre de projets: 144
Catégorie: Pop, Nombre de projets: 1302
Catégorie: Civic Design, Nombre de projets: 130
Catégorie: R&B, Nombre de projets

## Question 4

In [24]:
french_projects_before_2016 = collection.count_documents({
    'location.country': 'France',
    'created_at': {'$lt': pd.to_datetime('2016-01-01')}
})

print(f"Nombre de projets français avant 2016 : {french_projects_before_2016}")

Nombre de projets français avant 2016 : 0


## Question 5

In [25]:
us_projects_above_200k = collection.find({
    'location.country': 'United States',
    'goal': {'$gt': 200000}
})

for project in us_projects_above_200k:
    print(f"Nom: {project['name']}, Demande de financement: {project['goal']}")

## Question 6 

In [26]:
sport_projects_count = collection.count_documents({
    'name': {'$regex': 'Sport', '$options': 'i'}
})

print(f"Nombre de projets ayant 'Sport' dans leur nom : {sport_projects_count}")

Nombre de projets ayant 'Sport' dans leur nom : 502
